This notebook runs a `Qallse` model in simulation mode and shows how to simply visualize the results using utilities defined in module `hepqpr.qallse.plotting`.

# Import and setup

In [1]:
# import modules
import pandas as pd
import numpy as np

from hepqpr.qallse.plotting import *
from hepqpr.qallse import *
from hepqpr.qallse.dsmaker import create_dataset

# initialise the plotting module in "notebook" mode
set_notebook_mode()

# initialise the logging module
import logging
logging.basicConfig()
fmt = logging.Formatter("%(asctime)s.%(msecs)03d %(levelname)s %(name)s: %(message)s", datefmt='%H:%M:%S')
for handler in logging.getLogger().handlers: handler.setFormatter(fmt)
logging.getLogger('hepqpr').setLevel(logging.DEBUG)

# Define run config

In [2]:
# == DATASET CONFIG

dsmaker_config = dict(
    density=.2, # 1% 
)

# == INPUT CONFIG

# whether or not to add missing doublets to the input
add_missing = True 

# == RUN CONFIG

model_class = Qallse # model class to use
extra_config = dict() # configuration arguments overriding the defaults

# Generate the data

In [3]:
import tempfile

tempdir = tempfile.TemporaryDirectory()
print(f'using {tempdir.name}')
metas, path = create_dataset(output_path=tempdir.name, gen_doublets=True, random_seed=240834366, **dsmaker_config)

using /var/folders/7r/y3xzyywn4mg2tfhg0sgjqx_w0000gn/T/tmp5ly1lujc


13:56:55.868 DEBUG hepqpr.qallse.dsmaker.dsmaker: Loaded 120939 hits from /Users/parkerreid/hepqpr-qallse/src/hepqpr/qallse/dsmaker/data/event000001000.
13:56:55.904 DEBUG hepqpr.qallse.dsmaker.dsmaker: Filtered hits from barrel. Remaining hits: 65518.
13:56:55.959 DEBUG hepqpr.qallse.dsmaker.dsmaker: Dropped double hits. Remaining hits: 55446.
13:56:56.010 DEBUG hepqpr.qallse.dsmaker.dsmaker: High Pt hits: 32302/11055
13:56:56.426 DEBUG hepqpr.qallse.dsmaker.dsmaker:   num_hits=11055
13:56:56.427 DEBUG hepqpr.qallse.dsmaker.dsmaker:   num_tracks=1637
13:56:56.427 DEBUG hepqpr.qallse.dsmaker.dsmaker:   num_important_tracks=128
13:56:56.428 DEBUG hepqpr.qallse.dsmaker.dsmaker:   num_noise=2607
13:56:56.429 DEBUG hepqpr.qallse.dsmaker.dsmaker:   random_seed=240834366
13:56:56.430 DEBUG hepqpr.qallse.dsmaker.dsmaker:   time=2019-12-13T13:56:56.426711
13:57:06.452 INFO hepqpr.qallse.dsmaker.dsmaker: Doublets (len=387826) generated in f/var/folders/7r/y3xzyywn4mg2tfhg0sgjqx_w0000gn/T/tmp5ly

In [4]:
with open(path + '-meta.json') as f:
    print(f.read())

{
    "num_hits": 11055,
    "num_tracks": 1637,
    "num_important_tracks": 128,
    "num_noise": 2607,
    "random_seed": 240834366,
    "time": "2019-12-13T13:56:56.426711",
    "params": {
        "input_path": "/Users/parkerreid/hepqpr-qallse/src/hepqpr/qallse/dsmaker/data/event000001000",
        "output_path": "/var/folders/7r/y3xzyywn4mg2tfhg0sgjqx_w0000gn/T/tmp5ly1lujc",
        "density": 0.2,
        "high_pt_cut": 1.0,
        "double_hits_ok": false,
        "gen_doublets": true,
        "prefix": null,
        "random_seed": 240834366,
        "phi_bounds": null,
        "min_hits_per_track": 5
    }
}


# Execute the model

## Load the data

In [5]:
# load data
dw = DataWrapper.from_path(path)
doublets = pd.read_csv(path + '-doublets.csv')
if add_missing:
    doublets = dw.add_missing_doublets(doublets)
else:
    p, r, ms = dw.compute_score(doublets)
    print(f'got {len(doublets)}.')
    print(f'  Input precision (%): {p*100:.4f}, recall (%): {r*100:.4f}, missing: {len(ms)}')

got 387826 doublets.
  Input precision (%): 0.2461, recall (%): 99.3678
    New precision (%): 0.2476


## Build the model

In [6]:
%%time

# instantiate qallse
model = model_class(dw, **extra_config)
# build the qubo
model.build_model(doublets=doublets)
sliceContainer = model.to_qubo()

13:57:11.275 DEBUG hepqpr.qallse.qallse: using config:
13:57:11.276 DEBUG hepqpr.qallse.qallse:     cheat: False
13:57:11.276 DEBUG hepqpr.qallse.qallse:     max_layer_span: 2
13:57:11.277 DEBUG hepqpr.qallse.qallse:     num_multiplier: -1
13:57:11.277 DEBUG hepqpr.qallse.qallse:     qplet_max_dcurv: 0.0001
13:57:11.278 DEBUG hepqpr.qallse.qallse:     qplet_max_strength: -0.2
13:57:11.278 DEBUG hepqpr.qallse.qallse:     qubo_bias_weight: 0
13:57:11.279 DEBUG hepqpr.qallse.qallse:     qubo_conflict_strength: 1
13:57:11.279 DEBUG hepqpr.qallse.qallse:     rz_power: 1
13:57:11.281 DEBUG hepqpr.qallse.qallse:     strength_bounds: None
13:57:11.283 DEBUG hepqpr.qallse.qallse:     tplet_max_curv: 0.0008
13:57:11.283 DEBUG hepqpr.qallse.qallse:     tplet_max_drz: 0.1
13:57:11.284 DEBUG hepqpr.qallse.qallse:     volayer_power: 2
13:57:11.285 DEBUG hepqpr.qallse.qallse:     xy_power: 1
13:57:11.285 DEBUG hepqpr.qallse.qallse:     xy_relative_strength: 0.5
13:57:18.178 INFO hepqpr.qallse.qallse:

CPU times: user 1min 17s, sys: 888 ms, total: 1min 18s
Wall time: 1min 18s


## Sample the QUBO

Here, we use [_qbsolv_](https://github.com/dwavesystems/qbsolv) with default arguments. This means only classical algorithms.

In [7]:
%%time
# execute the qubo
responseContainer = model.sample_qubo_slices(Q=sliceContainer)
#response = model.sample_qubo_slices(Q=qslice)

0   0
{('24541_32436_39670', '24541_32436_39670'): 0, ('27100_33848_40266', '27100_33848_40266'): 0, ('41374_73431_80144', '41374_73431_80144'): 0, ('41374_73431_86625', '41374_73431_86625'): 0, ('24604_32035_39670', '24604_32035_39670'): 0, ('41374_80144_86625', '41374_80144_86625'): 0, ('41397_73022_79844', '41397_73022_79844'): 0, ('41397_73022_86354', '41397_73022_86354'): 0, ('41397_79844_86354', '41397_79844_86354'): 0, ('29603_36652_43664', '29603_36652_43664'): 0, ('33804_39927_78514', '33804_39927_78514'): 0, ('21467_29649_43055', '21467_29649_43055'): 0, ('29603_36652_75085', '29603_36652_75085'): 0, ('21467_29649_36688', '21467_29649_36688'): 0, ('27111_33845_71783', '27111_33845_71783'): 0, ('27111_33845_39968', '27111_33845_39968'): 0, ('27111_39968_71783', '27111_39968_71783'): 0, ('75116_82013_88948', '75116_82013_88948'): 0, ('45136_76604_90853', '45136_76604_90853'): 0, ('38991_45756_84949', '38991_45756_84949'): 0, ('82850_89627_95729', '82850_89627_95729'): 0, ('3671

13:58:32.664 INFO hepqpr.qallse.qallse: QUBO of size 3942 sampled in 2.55s (seed 1478738874).


0   1
{('19860_27268_34346', '19860_27268_34346'): 0, ('43203_75211_89394', '43203_75211_89394'): 0, ('44398_76308_90413', '44398_76308_90413'): 0, ('44398_83410_90414', '44398_83410_90414'): 0, ('44398_83404_90413', '44398_83404_90413'): 0, ('43203_75215_88645', '43203_75215_88645'): 0, ('44401_76305_83410', '44401_76305_83410'): 0, ('44401_76305_90414', '44401_76305_90414'): 0, ('44401_76308_83404', '44401_76308_83404'): 0, ('19979_26729_33917', '19979_26729_33917'): 0, ('40345_72090_78801', '40345_72090_78801'): 0, ('44401_76308_90413', '44401_76308_90413'): 0, ('44401_83410_90414', '44401_83410_90414'): 0, ('44401_83404_90413', '44401_83404_90413'): 0, ('19864_27247_34323', '19864_27247_34323'): 0, ('40355_72099_78803', '40355_72099_78803'): 0, ('21913_29888_37558', '21913_29888_37558'): 0, ('79910_86138_92160', '79910_86138_92160'): 0, ('37598_44342_75776', '37598_44342_75776'): 0, ('37598_75776_82985', '37598_75776_82985'): 0, ('22117_37595_44343', '22117_37595_44343'): 0, ('3759

13:58:36.266 INFO hepqpr.qallse.qallse: QUBO of size 3691 sampled in 6.08s (seed 1478738874).


0   2
{('22654_30202_44453', '22654_30202_44453'): 0, ('72845_79384_85723', '72845_79384_85723'): 0, ('22654_30202_37752', '22654_30202_37752'): 0, ('43942_75379_82252', '43942_75379_82252'): 0, ('72845_85723_91559', '72845_85723_91559'): 0, ('81244_87518_93677', '81244_87518_93677'): 0, ('81209_87483_93646', '81209_87483_93646'): 0, ('44880_83796_90703', '44880_83796_90703'): 0, ('20656_28183_34953', '20656_28183_34953'): 0, ('72850_79388_85731', '72850_79388_85731'): 0, ('43942_75379_89138', '43942_75379_89138'): 0, ('27363_33992_72140', '27363_33992_72140'): 0, ('72857_79389_85724', '72857_79389_85724'): 0, ('43942_82252_89138', '43942_82252_89138'): 0, ('27363_33992_40085', '27363_33992_40085'): 0, ('30151_37743_44895', '30151_37743_44895'): 0, ('72854_85723_91559', '72854_85723_91559'): 0, ('28121_34922_40806', '28121_34922_40806'): 0, ('81247_87928_93687', '81247_87928_93687'): 0, ('81258_87526_93688', '81258_87526_93688'): 0, ('28121_34923_40806', '28121_34923_40806'): 0, ('2736

13:58:41.500 INFO hepqpr.qallse.qallse: QUBO of size 6211 sampled in 11.31s (seed 1478738874).


0   3
{('75063_81956_88534', '75063_81956_88534'): 0, ('75502_89543_95669', '75502_89543_95669'): 0, ('75502_82745_89543', '75502_82745_89543'): 0, ('31883_38892_45673', '31883_38892_45673'): 0, ('31883_38892_77428', '31883_38892_77428'): 0, ('21030_28305_35049', '21030_28305_35049'): 0, ('42319_74384_80916', '42319_74384_80916'): 0, ('75534_82384_89235', '75534_82384_89235'): 0, ('31886_39278_45983', '31886_39278_45983'): 0, ('21328_28387_34599', '21328_28387_34599'): 0, ('31886_39275_77707', '31886_39275_77707'): 0, ('31886_39278_45981', '31886_39278_45981'): 0, ('75534_89235_95398', '75534_89235_95398'): 0, ('31886_39278_45978', '31886_39278_45978'): 0, ('81338_88006_94067', '81338_88006_94067'): 0, ('81335_87595_109498', '81335_87595_109498'): 0, ('23321_31396_45053', '23321_31396_45053'): 0, ('35637_41700_73329', '35637_41700_73329'): 0, ('23536_38524_45067', '23536_38524_45067'): 0, ('35637_41700_80075', '35637_41700_80075'): 0, ('35637_73329_80075', '35637_73329_80075'): 0, ('37

13:58:46.861 INFO hepqpr.qallse.qallse: QUBO of size 5568 sampled in 16.66s (seed 1478738874).


CPU times: user 16.2 s, sys: 481 ms, total: 16.7 s
Wall time: 16.8 s


## Parse the results

In [8]:
# get all output doublets
all_doublets = model.process_sample_slices(responseContainer=responseContainer)
# recreate tracks and resolve remaining conflicts
final_tracks, final_doublets = TrackRecreaterD().process_results(all_doublets)

13:58:46.896 INFO hepqpr.qallse.track_recreater: Found 0 conflicting doublets


# Evaluate the results

## Print statistics and scores

In [9]:
# stats about the qbsolv run
#en0 = dw.compute_energy(Q)
#en = response.record.energy[0]

#print(f'SAMPLE -- energy: {en:.4f}, ideal: {en0:.4f} (diff: {en-en0:.6f})')
#occs = response.record.num_occurrences
#print(f'          best sample occurrence: {occs[0]}/{occs.sum()}')

# scores
p, r, missings = dw.compute_score(final_doublets)
print(f'SCORE  -- precision (%): {p * 100}, recall (%): {r * 100}, missing: {len(missings)}')
trackml_score = dw.compute_trackml_score(final_tracks)
print(f'          tracks found: {len(final_tracks)}, trackml score (%): {trackml_score * 100}')

SCORE  -- precision (%): 93.20987654320987, recall (%): 95.46891464699684, missing: 43
          tracks found: 206, trackml score (%): 95.53058371167633


### Plot the results

You have the following at your disposal:
```python
iplot_results(dw, final_doublets, missings, dims=list('xy'))
iplot_results_tracks(dw, final_doublets, missings, dims=list('zr'))
iplot_results_any(dw, dw.real_doublets, dims=list('xy'))
```

For 3D plots, simply define `dims` as 3-dimensional. For example:
```python
iplot_results(dw, final_doublets, missings, dims=list('zxy'))
```

In [10]:
iplot_results(dw, final_doublets, missings, dims=list('xy'))

In [11]:
iplot_results(dw, final_doublets, missings, dims=list('zr'))

In [12]:
iplot_results(dw, final_doublets, missings, dims=list('zxy'))